In [65]:
%matplotlib inline
from io import open
import matplotlib.pyplot as plt
import csv
from textblob import TextBlob
import sklearn
import pickle
import numpy as np
import pandas as pd
from sklearn.feature_extraction.text import CountVectorizer, TfidfTransformer, TfidfVectorizer
from sklearn.naive_bayes import MultinomialNB
from sklearn.svm import SVC, LinearSVC
from sklearn.metrics import classification_report, f1_score, accuracy_score, confusion_matrix
from sklearn.pipeline import Pipeline
from sklearn.grid_search import GridSearchCV
from sklearn.cross_validation import StratifiedKFold, cross_val_score, train_test_split 
#from sklearn.model_selection import StratifiedKFold, cross_val_score, train_test_split 
from sklearn.tree import DecisionTreeClassifier 
from sklearn.learning_curve import learning_curve
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.porter import PorterStemmer
from nltk.tokenize import word_tokenize
import string
import os
import re
plt.style.use('ggplot')
pd.options.display.mpl_style = 'default'

/Users/darshansonde/anaconda2/envs/spam/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2862: FutureWarning: 
mpl_style had been deprecated and will be removed in a future version.
Use `matplotlib.pyplot.style.use` instead.

  exec(code_obj, self.user_global_ns, self.user_ns)


In [29]:
PATH=os.path.join(os.environ["ML_DATA_DIR"], "Spam")
os.listdir(PATH)

['.DS_Store', 'SMS2017India.csv', 'SMS_HamInfoSpam', 'SMS_Info_SubCategory']

HamInfo contains the dataset with ham/spam classification.

Info dataset contains only the spam data, but is further categorized into multiple categories.



# Data

In [31]:
haminfospam_file = os.path.join(PATH, "SMS_HamInfoSpam", "Train_Dataset.csv")
with open(haminfospam_file,encoding='latin1') as f:
    messages = pd.read_csv(f, sep=',', names=['label', 'message'],skiprows=1)

messages['message'] = messages['message'].map(lambda text:text)
messages.head()

label                                            message
0   ham                 oh how abt 2 days before Christmas
1  info  Welcome to OVATION HOLD R.No. 184, 114, 395, 3...
2  info  Thank you for using your ICICI bank CREDITcard...
3   ham  schedule a meeting with the entire team in the...
4   ham                                Tommy is my brother

In [38]:
messages.groupby('label').describe()

message                                                               
        count unique                                                top freq
label                                                                       
ham     10000   9977  Sorry for saying Sorry
I will drop u for sure
...    2
info    13375  13375  Bimal Auto Agency : Service of your car KA81W6...    1
spam     6625   6569  Delivered: Your package withStories of Tenali ...    4

In [37]:
print("Ham Messages Only")
for ix,m in  enumerate(messages[messages.label == 'ham'].message):
    print(ix, end='\t')
    print(m)


Ham Messages Only
0	oh how abt 2 days before Christmas
1	schedule a meeting with the entire team in the office tomorrow
2	Tommy is my brother
3	the meeting is scheduled by john
4	I will indeed! What time?
5	i will meet you on coming morning
6	i will meet john adams in bangalore
7	I have to catchup for dinner @ nite at his place
8	lets meet 29th after diwali
9	meeting is @ sharp 4am
10	drop off mary to john's home
11	wish nishu happy birthday
12	hey lets hv lunch together.
13	pay mortgage tomorrow
14	meeting is from 11am to 12 noon tomorrow
15	Ha ha..thnx buddy
16	birthday party on wed
17	What date you are coming to Goa?
18	abhanshu, mary and tom will meet in ccd
19	Transportation assistance to a neighboring community. Will no after visiting with Jamila?
20	remind me to see the doctor next month
21	Hi..I have to talk to you about something urgent. When can I call you?
22	check the emails received before 4pm
23	i have an appointment with dr. shastri tomorrow evening
24	call john between 

821	i need to speak to preeti
822	meet John at total mall
823	U can go..I will cala and convey my wishes before 10 2nite :)
824	ok.get 1 kilo each.
825	must pay my credit card bill of rs. 12 on monday
826	Does 5 sound good?
827	meet me on 8 dec
828	I am in Lakshadweep right now...don't hv much idea about this islandcan u meet me??
829	I would like to invite you for my daughter's 1st birthday party
830	Did you pay the credit card bill?
831	Sure..what time?
832	Hey..Please bring 2kg of wheat flour @3pm from Reliance Fresh and then drop my uncle @6pm@Kalamandir
833	bring nishu home
834	meet for 2 weekends
835	We reached home oscar.. Where are you guys??
836	meet john every second monday of every month
837	lets meet every month
838	hey can u turn on the outside lights? i'm gonna be back later tonight
839	Not coming.. Need to take rest.. Anything urgent
840	gr936522324632823
841	i will be late due to some personal work
842	Do we have any propel?
843	wish dr. lokendra shastri a very happy d

1988	shut down my system
1989	It's later today at 4pm.
1990	i will meet john on his birthday
1991	going to Las Vegas September 26th to the 29th
1992	lets meet after jan monday
1993	inform nishu about her dues
1994	I need to purchase monthly bus pass for this month by tomorrow eod.
1995	lets meet next month after 5th
1996	I am mathew's best man!!!
1997	every day i must meet john for 5 minutes.
1998	i must drop off mary to the tailor
1999	hey , How r u..?
2000	Okay, thank you for the reminder. when will it be available?
2001	lets meet today after morning breakfast
2002	night river fire 24th of September
2003	going to suwon with dipesh on the 15th. meet him there on wed
2004	John, Mary and Tom will meet me in total
2005	set up an appointment for tomorrow morning
2006	We're talking tomorrow cuz he wants to add more to the schedule and I'm trying to get him to pay for it
2007	Do you want to play some video games at my place tomorrow?
2008	Make a note to greet on the birth of his baby 2 mont

3172	gym at 5am tomorrow
3173	Possible to meet him?
3174	lets meet 31st of august
3175	Can we catch up? I need to talk about some things..
3176	my interview is on next wed
3177	tomorrow at 1 p.m. make an eye appointment
3178	Remember that dentist appointment for tooth pain at his place next Saturday around quarter to 6
3179	team lunch with mary is today from 12:15 to 2
3180	Please fix up an appointment with Manu's teacher on coming Tuesday. I forgot to do it myself :(
3181	Hey, my birthday is on Saturday and I'm having a party to celebrate. Do you want to come?
3182	With some chicken tikka kebabs :P
3183	Hey we've got that big test on Friday
3184	Will have one Appointment exactly after 10 days from today.
3185	i need to book tickets by this friday evening for going to delhi on 10th august
3186	Call 9437072921 on 10th morning and u can book
3187	Hillside tomorrow at 8 o'clock in the morning
3188	Do you want to go mountain biking with me on Saturday?
3189	I hv a meeting tomorrow@8
3190	p

4406	when i am at grocery remind me to check shopping list
4407	Do you want to watch the football game at my house on Sunday?
4408	I am going to the club tonight. You want to join ?
4409	i will meet you on third friday of every month
4410	need to send photos to john via whatsapp
4411	i shall meet the lawyer
4412	at 5 to 7 next monday there is a meeting
4413	i will be in office at 5:30pm. need to meet dr. aloknath de at 6pm there
4414	Oh so sorry dear..I have to attend likhita's Reception this Sunday at around 7 Pm..
4415	meet john during lunch tomorrow
4416	wish john birthday in the morning
4417	Vasanth is not reachable. Mostly he is out of town. Will get back.
4418	Yeah! I'll be there at 6:30
4419	meeting with their dad on September 9th 1:30 p.m. IST
4420	i need to go to the kitty party tomorrow at 5pm
4421	not possible I think :)
4422	wish nishu on her birthday at 12am
4423	btw what is ur father's name..?
4424	Its ok?wish her nw
4425	ok.. I think its gonna mess up
4426	john's birthda

5635	call lamia after 45 min
5636	We will come by 330 Dr. connor to review promotions
5637	How about lunch time?
5638	I will go bowling straight from office
5639	call zachary at 7a.m
5640	i will call you at 4 in the morning
5641	how about april 19th
5642	i have to pick up mary from her dance class
5643	Meanwhile,... Watching some fails on your tv????????
5644	respond to the emails
5645	Hi sir, can I have the drop location for the meru cab bill that you gave me?
5646	wish a happy birthday john
5647	Do u hv any problem if I drop u 30 mins prior to ur class??
5648	Smoothies tomorrow?
5649	Yeah, when does it start?
5650	i have an appointment with mr. john smith @ 5:35pm
5651	Hi..What are you doing this Friday?
5652	meet john on the eve of christmas this year
5653	Don't forget about your doctors appt rmrw!
5654	how about tomorrow
5655	will have lunch with all my friends on the coming weekend
5656	Can you pick up my clothes from the laundromat downtown? They'll be ready at 5pm.
5657	wedding 

6748	Remember that enquire his future plans 2moro by EOD
6749	Mary is not my wife anymore
6750	What time is good for you?
6751	Greet Abhijeet tonight
6752	reminder to write letter of recommendation
6753	For sure. See you then.
6754	Probably this Sunday, he gonna buy u ur engagement ring.
6755	its on Mondays at 6pm for 2hrs from January till 3rd week of march
6756	Hey! Wanan grab dinner in a bit?
6757	pick up milk on the way back
6758	I think it starts at around 3
6759	Wanna go to that new concert this Friday
6760	I will attend if u will join
6761	kailash and i should meet mary on his birthday
6762	I need to check on Harry near World Trade Centre about her health @ nite
6763	probably at dinner time
6764	utkarsh is leaving for airport today at 6 pm
6765	congratulate aloknath for being the corporate vp of samsung
6766	need to attend the call at 4pm
6767	Remind me to make party preparations in Bangalore with dad tmrw
6768	at 5 pm, pickup kevin
6769	i will be in bangalore on friday evening.

7914	Remember that the board meeting is at 2:30 pm on sunday
7915	Lets meet in hangout
7916	the meeting can be on any day next week
7917	Sure what do you wanna do?
7918	mary's party on 6th. attend the party
7919	Ok. Meet me near ccd after 20 mins.
7920	drop mary to the wedding party
7921	call mr. and mrs. abhanshu to wish them happy married life
7922	lets meet this morning after 8
7923	By what time you will be in office
7924	start the fridge
7925	Susan will meet me in the evening
7926	I am not in office right now. But I will be there by 11
7927	Do you want to go shopping downtown with me tomorrow?
7928	It's in Indira Nagar.
7929	meeting will be on any weekday next week
7930	Alright see you then
7931	lets see minions tomorrow
7932	go for a movie tonight with mary 9pm-11pm
7933	to pay school fees
7934	Can u drop my daughter to school
7935	Heyy dinner at my place tomorrow?
7936	Noo.. I heard he is busy with his premed exams
7937	party is on this 17th
7938	pat rohini on the back for a good

9068	catch mary for dinner
9069	call bank on monday noon
9070	Hey!! Did u have an account in Hangout
9071	Ahh, ok. That will work
9072	meet john's sister in the parlor
9073	Tomorrowanytime after evening.
9074	6pm, there's a great place on Pacific that I think you would like
9075	Ok, sounds good, see you then.
9076	Catchup for discussion on the day after Thanksgiving
9077	bring rs. 10,000 home for bill payment
9078	Ok, that's fine, I'll drop you off.
9079	Are you still coming to my sister's graduation ceremony?
9080	birthday party @ 7
9081	i will call u aftr demo on fri
9082	pay rs 55,000 online as security deposit before 14th
9083	Hey I was just thinking about you. Bobby texted me this morning about the chair. I'm good here. You?
9084	session with Pat at 11 November 15th
9085	lets meet mondays at 6pm for 2hours starting january through 2nd week of march
9086	john and mary are in bangalore. meet him there
9087	when is ur train
9088	I have to check on Harry abt his well being
9089	What 

In [39]:
print("Info Messages Only")
for ix,m in  enumerate(messages[messages.label == 'info'].message):
    print(ix, end='\t')
    print(m)


Info Messages Only
0	Welcome to OVATION HOLD R.No. 184, 114, 395, 378 Ch.In 2014-10-21 3:53 Ch.out 2014-11-01 12:00.
1	Thank you for using your ICICI bank CREDITcard ending 5253 for Rs. 2520.00 in ALIKE at Snapdeal on 2013-05-31 21:35
2	The PNR for your Air India Flt 7I115 for PGH-BDQ on 2014-06-25 at 4:18 hrs  is PQPG4H. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
3	Bimal Auto Agency : Service of your car KA52C8378 is due in 72 days on 2015-01-28. Please contact us at 9411881245 to book a service.
4	Appointment with Dr Clayton in Pune on 2011-08-09 at 12:16 is confirmed. For queries call 1800 8126 6547. Your appt. might get delayed in case the doctor is attending an emergency.
5	Maha Veer Auto Agency : Service of your car KA88N4761 is due in 56 days on 2013-12-06. Please contact us at 9484286846 to book a service.
6	Dear Guest, Thanks for choosing Forlini's Restaurant. Order ID 4117. Delivery by 2012-09-15 10:33. Enjoy 22% discount on your next purchase. Code OA58

558	Hi Customer, Booking ID: WYYDKU7. Seats: SILVER-K7, 1 seat(s) for The Purge: Election Year on 2009-11-18 4:37 at Anjan Digital 4K A/C Cinema: Magadi Road. Please carry your CC/DC card which was used for booking tickets.
559	PNR:3788631224,TRAIN:25725,DOJ:2015-04-04,AC3,BPA-BTH,Dep:9:10, James,B6 65 , Fare:4965,SC:10.0+PG+INS
560	Bimal Auto Agency : Service of your car KA56D4133 is due in 88 days on 2014-05-11. Please contact us at 9724386332 to book a service.
561	Dear Guest, Thanks for choosing Grill restaurant. Order ID 1127. Delivery by 2009-08-25 15:15. Enjoy 3% discount on your next purchase. Code LD0HDS. T&C.
562	* KSRTC m-Ticket *  from: TRICHY to: SRIKALAHASTI PsngrName: Parker TripCode: 1322TRISRI PNR No.: J16221523 JnyDate: 2013-07-13 DepTime: 13:22  SeatNo.: 35, 41, 17, 20, 54, 29  Class: AC chair  BoardingPt: TRICHY MG Road Txn Password: 5826 . Please carry your photo ID during journey. T&C apply. Visit  www.ksrtc.in
563	Maha Veer Auto Agency : Service of your car KA58P

1673	[Extreme Pita] Hi Miguel, your reservation is confirmed for 29 people on 2010-04-15 at 1:58. We can hold your table for a maximum of 38 mins.
1674	Welcome to El Meson Sandwiches R.No. 372 Ch.In 2011-08-28 18:50 Ch.out 2011-08-29 12:00.
1675	The PNR for your SPICE JET Flt 2E426 for KLH-MZU on 2013-12-18 at 8:42 hrs  is P6HAZ9. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
1676	* KSRTC m-Ticket *  from: KIAL to: Ernakulam PsngrName: Oscar TripCode: 1816KIAErn PNR No.: J97118044 JnyDate: 2009-11-19 DepTime: 18:16  SeatNo.: 26, 22  Class: AC chair  BoardingPt: KIAL Rly Station Txn Password: 5575 . Please carry your photo ID during journey. T&C apply. Visit  www.ksrtc.in
1677	PNR:4311241773,TRAIN:34523,DOJ:2012-06-29,AC3,BTX-BWSN,Dep:23:25, Colin,B1 30 , Fare:7229,SC:10.0+PG+INS
1678	Dear Guest, Thanks for choosing The George Prime Steakhouse. Order ID 7656. Delivery by 2011-12-20 11:19. Enjoy 23% discount on your next purchase. Code X59TFB. T&C.
1679	Thank you for c

2855	Thank you for using your HDFC bank CREDITcard ending 7787 for Rs. 422.00 in KOLHAPUR at Snapdeal on 2015-03-20 14:21
2856	Welcome to Ain Arnat Airport R.No. 152, 170, 139, 364 Ch.In 2013-04-22 19:53 Ch.out 2013-05-14 12:00.
2857	Hi Customer, Booking ID: WRW4LA3. Seats: STANDARD-A9,A10,A11, 3 seat(s) for Arrival on 2014-05-03 1:37 at PVR: Arena Mahadevapura, Bengaluru. Please carry your CC/DC card which was used for booking tickets.
2858	Hi Customer, Booking ID: WCUNTB4. Seats: SILVER-G16,G17,G18, 3 seat(s) for Boo! A Madea Halloween on 2013-09-08 16:32 at Gopalan Cinemas: Arcade Mall, Mysore Road. Please carry your CC/DC card which was used for booking tickets.
2859	YourBus (PAYYANUR-UDUPI 17:51) left  8th Mile Stone at 18:51 approx. It is running as per schedule.Track YourBus at http://goo.gl/R0m5jx
2860	Hi Customer, Booking ID: W0K9D2Q. Seats: STANDARD-G5,G6, 2 seat(s) for The Girl on the Train on 2015-01-27 2:53 at PVR: Market City, Bengaluru. Please carry your CC/DC card which

4007	* KSRTC m-Ticket *  from: Mangaluru to: HASSAN PsngrName: Dustin TripCode: 1927ManHAS PNR No.: J29404292 JnyDate: 2013-10-05 DepTime: 19:27  SeatNo.: 4, 49, 7, 43, 12, 17, 52, 21, 25  Class: Non-AC chair  BoardingPt: Mangaluru MG Road Txn Password: 7855 . Please carry your photo ID during journey. T&C apply. Visit  www.ksrtc.in
4008	PNR:4712612752,TRAIN:4368,DOJ:2015-08-18,FC,BJW-BDN,Dep:0:53, Andres,F8 37 , Fare:4271,SC:10.0+PG+INS
4009	Thank you for choosing ucabs for 2014-08-21 at 7:38. Cab:KA12J2162 , Chauffer: Benjamin, Cell: 9278748856 will reach you. T&C apply, visit www.ucabs.com
4010	PNR:7672454438,TRAIN:52442,DOJ:2014-06-12,FC,ARW-BDH,Dep:0:51, Jaden,F9 88 , Fare:5785,SC:10.0+PG+INS
4011	DEAR Chase, THANK YOU FOR YOUR BOOKING (ORDER ID: 53131), YOUR ORDER HAS BEEN ASSIGNED TO Marcos(9538882665) AND APPOINTMENT FOR SAMPLE COLLECTION IS SCHEDULED ON 2012-05-31 at 18:27. FOR ASSISTANCE WHATSAPP US ON 8845882852.
4012	YourBus (THRISSUR-Dharmastala 5:48) left  Agara Flyover a

...

7694	* KSRTC m-Ticket *  from: SRINGERI to: Kundapura PsngrName: Dillon TripCode: 1034SRIKun PNR No.: J49477279 JnyDate: 2014-01-21 DepTime: 10:34  SeatNo.: 16, 9, 18, 53  Class: AC chair  BoardingPt: SRINGERI Residency Road Txn Password: 5182 . Please carry your photo ID during journey. T&C apply. Visit  www.ksrtc.in
7695	Appointment with Dr Carson in AGUMBE on 2011-07-25 at 13:34 is confirmed. For queries call 1800 5461 4651. Your appt. might get delayed in case the doctor is attending an emergency.
7696	Welcome to Ching Farm Animal Rescue and Sanctuary R.No. 505, 571, 169 Ch.In 2015-02-07 5:19 Ch.out 2015-02-15 12:00.
7697	DEAR Zachary, THANK YOU FOR YOUR BOOKING (ORDER ID: 45617), YOUR ORDER HAS BEEN ASSIGNED TO Giovanni(9855525743) AND APPOINTMENT FOR SAMPLE COLLECTION IS SCHEDULED ON 2010-11-22 at 17:18. FOR ASSISTANCE WHATSAPP US ON 8314837728.
7698	Bimal Auto Agency : Service of your car KA72H3577 is due in 22 days on 2013-11-09. Please contact us at 9571634421 to book a servic

8898	[Aberdeen Angus Steak Houses] Hi Devon, your reservation is confirmed for 14 people on 2011-08-25 at 8:20. We can hold your table for a maximum of 29 mins.
8899	Thank you for choosing Ola for 2011-04-26 at 16:26. Cab:KA82I1265 , Chauffer: Joel, Cell: 9322422558 will reach you. T&C apply, visit www.Ola.com
8900	Hi Customer, Booking ID: W9298YT. Seats: SILVER-B13,B14,B15,B16,B17,B18,B19, 7 seat(s) for Independence Day: Resurgence on 2011-05-04 8:36 at INOX: Forum Neighbourhood Mall, Whitefield. Please carry your CC/DC card which was used for booking tickets.
8901	PNR:5318141671,TRAIN:11623,DOJ:2014-07-14,SL,BHLA-BWM,Dep:8:12, Dawson,S1 44 , Fare:1020,SC:10.0+PG+INS
8902	Thank you for choosing AirportTaxi for 2013-08-15 at 7:56. Cab:KA53L2465 , Chauffer: Joshua, Cell: 9813851131 will reach you. T&C apply, visit www.AirportTaxi.com
8903	The PNR for your INDIGO Flt 3P864 for DED-JRH on 2013-11-06 at 2:11 hrs  is R1XST3. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
8

10094	Repair ref.no for your car is JC76828313 opened on 2014-09-13 0:12hrs,ETD of your car is 2014-09-14 8:21hrs and est.repair amt is Rs.596 Rgds, True Value
10095	YourBus (Kozhikode-Shivamogga 15:57) left  Agara Flyover at 16:57 approx. It is running as per schedule.Track YourBus at http://goo.gl/R0m5jx
10096	Lakshmi Auto Agency : Service of your car KA48A8276 is due in 66 days on 2011-04-22. Please contact us at 9817743422 to book a service.
10097	[Essie 's Original Hot Dog shop] Hi Jackson, your reservation is confirmed for 22 people on 2015-02-02 at 12:32. We can hold your table for a maximum of 23 mins.
10098	[Lee's Tavern] Hi John, your reservation is confirmed for 26 people on 2015-02-18 at 23:58. We can hold your table for a maximum of 37 mins.
10099	Repair ref.no for your car is JC76613176 opened on 2014-01-01 2:28hrs,ETD of your car is 2014-01-02 10:52hrs and est.repair amt is Rs.1443 Rgds, Maruti Auto Agency
10100	The PNR for your INDIGO Flt 3Z161 for JRH-NAG on 2010-12-30

11290	Thank you for choosing KSRTC for 2015-02-25 at 0:46. Cab:KA28Z7423 , Chauffer: Ruben, Cell: 9383336431 will reach you. T&C apply, visit www.KSRTC.com
11291	[Maoz Vegetarian] Hi Colby, your reservation is confirmed for 8 people on 2012-06-01 at 14:30. We can hold your table for a maximum of 7 mins.
11292	The PNR for your AirAsia Flt 6L128 for DIB-PAT on 2010-01-15 at 15:31 hrs  is CVBDQB. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
11293	* KSRTC m-Ticket *  from: Pune to: KOLAR PsngrName: Sebastian TripCode: 1315PunKOL PNR No.: J46163335 JnyDate: 2013-03-05 DepTime: 13:15  SeatNo.: 34, 36, 37, 39, 17, 59  Class: AC Sleeper  BoardingPt: Pune MG Road Txn Password: 3472 . Please carry your photo ID during journey. T&C apply. Visit  www.ksrtc.in
11294	Welcome to RANGE FC R.No. 324, 103 Ch.In 2013-10-05 16:12 Ch.out 2013-10-16 12:00.
11295	Thank you for choosing radiocabs for 2015-03-28 at 0:18. Cab:KA18A6413 , Chauffer: Tristan, Cell: 9747367142 will reach you. T&

12526	The PNR for your INDIGO Flt 2C172 for KLH-SUN on 2014-11-06 at 5:51 hrs  is H4RUE7. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
12527	YourBus (PALAKKAD-KIAL 19:26) left  Goragunte Palya at 20:26 approx. It is running as per schedule.Track YourBus at http://goo.gl/R0m5jx
12528	Welcome to Liquor shop R.No. 345, 195 Ch.In 2014-09-13 22:57 Ch.out 2014-09-18 12:00.
12529	Thank you for choosing radiocabs for 2015-06-02 at 0:38. Cab:KA86C2127 , Chauffer: Isaiah, Cell: 9312838315 will reach you. T&C apply, visit www.radiocabs.com
12530	PNR:8373734647,TRAIN:4245,DOJ:2009-12-20,SL,ALNI-BBAI,Dep:22:39, Noah,S9 13 , Fare:7463,SC:10.0+PG+INS
12531	Bimal Auto Agency : Service of your car KA82J6244 is due in 73 days on 2010-01-17. Please contact us at 9581142126 to book a service.
12532	Welcome to Saint Mary-of-the-Woods College R.No. 472, 224, 415, 383 Ch.In 2009-11-20 12:14 Ch.out 2009-11-29 12:00.
12533	YourBus (ALIKE-Panaji Goa 15:52) left  Agara Flyover at 16:52 approx

In [54]:
info_subcat_file = os.path.join(PATH, "SMS_Info_SubCategory", "Train_info_dataset.csv")
with open(info_subcat_file,encoding='latin1') as f:
    infos = pd.read_csv(f, sep=',', names=['label', 'message'],skiprows=1)

infos.describe()

label                                            message
count    12000                                              12000
unique      12                                              12000
top     Expiry  Maha Veer Auto Agency : Service of your car KA...
freq      1000                                                  1

In [49]:
# check if each info in dataset has an entry in subcat
matches = 0
nmatches = 0

messages_info = messages[messages.label == 'info']
for ix,m in  enumerate(messages_info.message):
    matched = 0
    for jx, im in enumerate(infos.message):
        if(m == im):
            matches = matches+1
            matched = 1
            print("Matched:",ix,jx, m)
            break
    if(matched == 0):
        print("Not Matched:" , m)
        nmatches = nmatches+1
print(f'Matches {matches}')
print(f'Not Mat {nmatches}')


Not Matched: Welcome to OVATION HOLD R.No. 184, 114, 395, 378 Ch.In 2014-10-21 3:53 Ch.out 2014-11-01 12:00.
Not Matched: Thank you for using your ICICI bank CREDITcard ending 5253 for Rs. 2520.00 in ALIKE at Snapdeal on 2013-05-31 21:35
Not Matched: The PNR for your Air India Flt 7I115 for PGH-BDQ on 2014-06-25 at 4:18 hrs  is PQPG4H. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
Matched: 3 1103 Bimal Auto Agency : Service of your car KA52C8378 is due in 72 days on 2015-01-28. Please contact us at 9411881245 to book a service.
Not Matched: Appointment with Dr Clayton in Pune on 2011-08-09 at 12:16 is confirmed. For queries call 1800 8126 6547. Your appt. might get delayed in case the doctor is attending an emergency.
Not Matched: Maha Veer Auto Agency : Service of your car KA88N4761 is due in 56 days on 2013-12-06. Please contact us at 9484286846 to book a service.
Not Matched: Dear Guest, Thanks for choosing Forlini's Restaurant. Order ID 4117. Delivery by 2012-09-

Not Matched: Repair ref.no for your car is JC43736167 opened on 2014-12-09 10:33hrs,ETD of your car is 2014-12-10 12:46hrs and est.repair amt is Rs.2982 Rgds, Hyundai Auto Agency
Not Matched: Welcome to HOMETOWN BC R.No. 201, 124, 213 Ch.In 2010-08-12 13:39 Ch.out 2010-08-24 12:00.
Not Matched: [Joe Muggs] Hi Stephen, your reservation is confirmed for 5 people on 2010-12-20 at 13:26. We can hold your table for a maximum of 10 mins.
Not Matched: Dear Guest, Thanks for choosing Haldiram 's. Order ID 3447. Delivery by 2010-11-01 10:53. Enjoy 19% discount on your next purchase. Code R5M4ON. T&C.
Not Matched: Welcome to Biodynamic Massage salon R.No. 115, 193, 431, 463 Ch.In 2010-12-02 16:15 Ch.out 2010-12-18 12:00.
Not Matched: Dear Guest, Thanks for choosing Dracula 's Cabaret Restaurant. Order ID 7187. Delivery by 2014-09-16 22:42. Enjoy 10% discount on your next purchase. Code EWXKD7. T&C.
Not Matched: Welcome to varandah R.No. 307, 268 Ch.In 2009-10-29 2:48 Ch.out 2009-11-27 12:00.
Mat

Not Matched: Welcome to Faro Airport R.No. 358, 375 Ch.In 2009-10-31 16:11 Ch.out 2009-11-01 12:00.
Not Matched: Welcome to DIME BK R.No. 138 Ch.In 2012-02-20 1:12 Ch.out 2012-03-07 12:00.
Not Matched: Dear Guest, Thanks for choosing PizzaRev. Order ID 6765. Delivery by 2014-02-16 5:29. Enjoy 24% discount on your next purchase. Code C6SOET. T&C.
Not Matched: [Perlan] Hi Dustin, your reservation is confirmed for 26 people on 2014-04-20 at 22:30. We can hold your table for a maximum of 18 mins.
Not Matched: DEAR Lucas, THANK YOU FOR YOUR BOOKING (ORDER ID: 47243), YOUR ORDER HAS BEEN ASSIGNED TO Giovanni(9433175162) AND APPOINTMENT FOR SAMPLE COLLECTION IS SCHEDULED ON 2012-08-14 at 15:14. FOR ASSISTANCE WHATSAPP US ON 8762716674.
Matched: 197 10744 Repair ref.no for your car is JC32283536 opened on 2009-12-17 8:13hrs,ETD of your car is 2009-12-18 14:24hrs and est.repair amt is Rs.1766 Rgds, Maha Veer Auto Agency
Not Matched: YourBus (KANNUR-MANIPAL 0:21) left  8th Mile Stone at 1:21 app

Matched: 330 11940 Thank you for choosing Ola for 2015-04-12 at 7:17. Cab:KA55Z8748 , Chauffer: Nolan, Cell: 9233856821 will reach you. T&C apply, visit www.Ola.com
Not Matched: * KSRTC m-Ticket *  from: Shivamogga to: KUMBAKONAM PsngrName: Colby TripCode: 235ShiKUM PNR No.: J85414863 JnyDate: 2013-04-09 DepTime: 2:35  SeatNo.: 23  Class: AC Sleeper  BoardingPt: Shivamogga Residency Road Txn Password: 6816 . Please carry your photo ID during journey. T&C apply. Visit  www.ksrtc.in
Matched: 332 560 Thank you for choosing Uber for 2014-12-07 at 2:47. Cab:KA35E4677 , Chauffer: Carter, Cell: 9167131676 will reach you. T&C apply, visit www.Uber.com
Not Matched: Thank you for using your HDFC bank CREDITcard ending 4522 for Rs. 1922.00 in Kozhikode at Paytm SELLER SERVICES on 2011-11-26 14:17
Matched: 334 5941 Hi Customer, Booking ID: WWFI85H. Seats: STANDARD-A9,A10,A11,A12,A13, 5 seat(s) for The Conjuring 2 on 2013-06-04 6:11 at PVR: Vaishnavi Sapphire Mall, Bengaluru. Please carry your CC/D

Matched: 496 3183 Dear Guest, Thanks for choosing Hoka Hoka Bento. Order ID 2781. Delivery by 2011-10-23 22:39. Enjoy 8% discount on your next purchase. Code OZVJ02. T&C.
Not Matched: PNR:1358361313,TRAIN:77216,DOJ:2014-12-06,AC3,AMC-BILD,Dep:6:26, Griffin,B4 12 , Fare:9165,SC:10.0+PG+INS
Matched: 498 6460 Welcome to Hokuetsu Bank R.No. 254, 534 Ch.In 2011-12-26 16:18 Ch.out 2011-12-28 12:00.
Not Matched: Hi Customer, Booking ID: W79MLBO. Seats: STANDARD-F12,F13,F14,F15,F16,F17, 6 seat(s) for Trolls on 2012-07-29 17:25 at Lakshmi Digital 4K Cinema: Tavarekere. Please carry your CC/DC card which was used for booking tickets.
Not Matched: Repair ref.no for your car is JC66753313 opened on 2014-10-20 19:48hrs,ETD of your car is 2014-10-21 17:23hrs and est.repair amt is Rs.2109 Rgds, Maruti Auto Agency
Not Matched: [Pizza Corner] Hi Kaleb, your reservation is confirmed for 10 people on 2014-03-27 at 19:56. We can hold your table for a maximum of 18 mins.
Matched: 502 10666 Bill dated 2013-

...

Not Matched: PNR:4381611845,TRAIN:62831,DOJ:2012-06-18,AC3,AME-BN,Dep:8:11, Connor,B6 83 , Fare:9212,SC:10.0+PG+INS
Not Matched: The PNR for your AirAsia Flt 2A685 for BUP-BHJ on 2012-12-25 at 13:20 hrs  is NT92Q3. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
Not Matched: Hi Customer, Booking ID: WWEWDF0. Seats: STANDARD-M16,M17,M18, 3 seat(s) for Sausage Party on 2010-05-21 15:22 at PVR: Orion Gold, Rajajinagar. Please carry your CC/DC card which was used for booking tickets.
Not Matched: The PNR for your Air India Flt 4Z168 for PUI-DMU on 2009-11-10 at 10:55 hrs  is ND8O89. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
Not Matched: PNR:2565141111,TRAIN:4752,DOJ:2014-01-19,FC,AGD-BVN,Dep:17:16, Gerardo,F8 41 , Fare:3332,SC:10.0+PG+INS
Matched: 12608 4315 Thank you for choosing Meru for 2015-02-07 at 23:30. Cab:KA52K5557 , Chauffer: Mitchell, Cell: 9132735688 will reach you. T&C apply, visit www.Meru.com
Matched: 12609 788 Thank you for choosing K

Not Matched: Bill dated 2012-03-21 for Rs 1024 has been generated for your Idea fixedline/broadband relationship no. 48271245. The same will reach you by 2012-03-24. Due date: 2012-04-05.
Not Matched: Thank you for choosing taxiforsure for 2012-06-19 at 15:10. Cab:KA74Y5253 , Chauffer: Edgar, Cell: 9482117885 will reach you. T&C apply, visit www.taxiforsure.com
Not Matched: YourBus (PONDICHERRY-KASARGOD 21:32) left  Electronic City at 22:32 approx. It is running as per schedule.Track YourBus at http://goo.gl/R0m5jx
Not Matched: Appointment with Dr Steven in KARAIKUDI on 2014-04-23 at 10:12 is confirmed. For queries call 1800 4267 7221. Your appt. might get delayed in case the doctor is attending an emergency.
Matched: 12760 5663 True Value : Service of your car KA87U5344 is due in 45 days on 2010-05-23. Please contact us at 9661643811 to book a service.
Not Matched: Thank you for choosing radiocabs for 2014-07-26 at 18:50. Cab:KA61R5772 , Chauffer: Jaiden, Cell: 9636758824 will reach y

Not Matched: DEAR Julian, THANK YOU FOR YOUR BOOKING (ORDER ID: 63317), YOUR ORDER HAS BEEN ASSIGNED TO Troy(9452653181) AND APPOINTMENT FOR SAMPLE COLLECTION IS SCHEDULED ON 2010-01-02 at 12:30. FOR ASSISTANCE WHATSAPP US ON 8874478284.
Matched: 12907 10718 Thank you for choosing Uber for 2015-01-20 at 5:38. Cab:KA37I3352 , Chauffer: Jake, Cell: 9343111155 will reach you. T&C apply, visit www.Uber.com
Not Matched: PNR:7334481571,TRAIN:5546,DOJ:2013-12-06,SL,BBM-BHTA,Dep:22:41, Peter,S6 18 , Fare:6024,SC:10.0+PG+INS
Not Matched: PNR:6826121273,TRAIN:33241,DOJ:2009-10-08,AC3,ARCL-BLMK,Dep:20:50, Adam,B3 19 , Fare:6537,SC:10.0+PG+INS
Matched: 12910 78 Hi Customer, Booking ID: W08U4VV. Seats: STANDARD-L2,L3,L4,L5,L6,L7,L8, 7 seat(s) for Ride Along 2 on 2012-11-21 2:10 at Fun Cinemas: Sigma Mall, Bengaluru. Please carry your CC/DC card which was used for booking tickets.
Matched: 12911 2995 [The New Riverside Cafe] Hi Nathaniel, your reservation is confirmed for 4 people on 2014-04-01 at 3

Not Matched: Dear Guest, Thanks for choosing jims tacos. Order ID 3644. Delivery by 2011-09-28 15:56. Enjoy 18% discount on your next purchase. Code OPPNTC. T&C.
Not Matched: PNR:3826418481,TRAIN:41822,DOJ:2012-10-25,FC,ADL-BHNE,Dep:5:28, Kaiden,F8 65 , Fare:3674,SC:10.0+PG+INS
Not Matched: The PNR for your SPICE JET Flt 7T424 for DMU-WGC on 2013-01-08 at 21:25 hrs  is ERQSGG. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
Matched: 13061 577 Thank you for choosing KSRTC for 2014-02-21 at 13:37. Cab:KA11V2831 , Chauffer: Mitchell, Cell: 9752171767 will reach you. T&C apply, visit www.KSRTC.com
Not Matched: Hi Customer, Booking ID: W0K8Y61. Seats: STANDARD-A5,A6,A7,A8,A9,A10, 6 seat(s) for Bad Moms on 2010-10-31 20:35 at INOX: Garuda Mall, Magrath Road. Please carry your CC/DC card which was used for booking tickets.
Not Matched: Welcome to Cape R.No. 538, 475, 558 Ch.In 2015-01-29 0:23 Ch.out 2015-02-19 12:00.
Matched: 13064 2713 Hi Customer, Booking ID: WC6JOB2. Seats

Not Matched: Bill dated 2009-11-05 for Rs 706 has been generated for your Airtel fixedline/broadband relationship no. 13226146. The same will reach you by 2009-11-08. Due date: 2009-11-20.
Not Matched: The PNR for your JET Airways Flt 4R827 for BOM-SHL on 2011-05-04 at 23:37 hrs  is RSZOKN. Tip: Check PNR status and book using MakeMyTrip App!. Thank you.
Not Matched: Welcome to Foot massage salon R.No. 454 Ch.In 2013-06-01 14:16 Ch.out 2013-06-14 12:00.
Matched: 13228 6610 Bill dated 2010-09-11 for Rs 311 has been generated for your Idea fixedline/broadband relationship no. 28572553. The same will reach you by 2010-09-14. Due date: 2010-09-26.
Not Matched: Appointment with Dr Kaleb in Dharmastala on 2013-01-04 at 0:47 is confirmed. For queries call 1800 7378 7687. Your appt. might get delayed in case the doctor is attending an emergency.
Matched: 13230 7336 Thank you for choosing taxiforsure for 2013-12-24 at 21:19. Cab:KA86B2722 , Chauffer: Israel, Cell: 9335222885 will reach you. T&C

In [ ]:
#Matches 4193
#Not Mat 9182

In [50]:
infos.label.value_counts()

Expiry         1000
Appointment    1000
Payment        1000
Movie          1000
Train          1000
Delivery       1000
Cab            1000
Flight         1000
Hotel          1000
PickUp         1000
Reservation    1000
Bus            1000
Name: label, dtype: int64

In [53]:
for cat in infos.label.unique():
    print(infos[infos.label == cat].head())

       label                                            message
0   Delivery  Dear Guest, Thanks for choosing The Edison. Or...
18  Delivery  Dear Guest, Thanks for choosing Paris Baguette...
28  Delivery  Dear Guest, Thanks for choosing Street food st...
31  Delivery  Dear Guest, Thanks for choosing Abu Nawas. Ord...
66  Delivery  Dear Guest, Thanks for choosing Top of the Wor...
     label                                            message
1    Hotel  Welcome to Southern University at Shreveport R...
9    Hotel  Welcome to Telecaf R.No. 524, 573, 519 Ch.In 2...
46   Hotel  Welcome to picnic spot R.No. 560, 139, 396 Ch....
56   Hotel  Welcome to Brussels South Charleroi Airport R....
111  Hotel  Welcome to Laughing Falls R.No. 504, 106, 533,...
      label                                            message
2   Payment  Bill dated 2013-01-14 for Rs 626 has been gene...
3   Payment  Bill dated 2014-11-30 for Rs 323 has been gene...
13  Payment  Bill dated 2012-09-07 for Rs 501 has been 

considering that info categorization is a subproblem of main classification. and most of info messages seem repeated and might not add that much value. 4193 samples are there in the main set. ignoring the subcat dataset for now.

# Filtering

lets filter and recreate all the lines into spam, info and ham according to our rules


In [71]:
messages.to_csv("outfile.tsv", sep='\t', encoding='utf-8', index=False)